In [3]:
import os
os.chdir('..')

In [4]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

In [5]:
import plotly.offline as pyo
pyo.init_notebook_mode()

In [6]:
from DataManager.WindTK import WindTKAPI

In [7]:
latitude = 37.9543963
longitude = -91.7831068
year = 2013

In [8]:
windtk_api = WindTKAPI()

In [6]:
windtk_api.calibrate(latitude, longitude, year)
windtk_api.download()
windtk_api.tabelize()

In [7]:
windtk_api.download()

WindTK Data saved as CSV successfully.


In [8]:
windtk_api.tabelize()

In [7]:
summer_data = windtk_api.get_dataframe(t1=(7,1), t2=(7,7))
winter_data = windtk_api.get_dataframe(t1=(1,1), t2=(1,7))

In [8]:
pd.set_option('display.max_columns', None)

In [9]:
summer_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 336 entries, 0 to 335
Data columns (total 40 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   index                       336 non-null    int64  
 1   Year                        336 non-null    int64  
 2   Month                       336 non-null    int64  
 3   Day                         336 non-null    int64  
 4   Hour                        336 non-null    int64  
 5   Minute                      336 non-null    int64  
 6   surface_air_pressure        336 non-null    int64  
 7   air_pressure_100m           336 non-null    int64  
 8   air_pressure_200m           336 non-null    int64  
 9   relative_humidity_2m        336 non-null    float64
 10  surface_precipitation_rate  336 non-null    float64
 11  wind_speed_10m              336 non-null    float64
 12  wind_speed_40m              336 non-null    float64
 13  wind_speed_60m              336 non

In [10]:
summer_data

index  Year  Month  Day  Hour  Minute  surface_air_pressure   
0     8688  2013      7    1     0       0                 97680  \
1     8689  2013      7    1     0      30                 97700   
2     8690  2013      7    1     1       0                 97690   
3     8691  2013      7    1     1      30                 97720   
4     8692  2013      7    1     2       0                 97720   
..     ...   ...    ...  ...   ...     ...                   ...   
331   9019  2013      7    7    21      30                 97950   
332   9020  2013      7    7    22       0                 97970   
333   9021  2013      7    7    22      30                 97980   
334   9022  2013      7    7    23       0                 97960   
335   9023  2013      7    7    23      30                 97990   

     air_pressure_100m  air_pressure_200m  relative_humidity_2m   
0                96520              95410                 95.89  \
1                96550              95430                 95.81   
2                96530              95420                 94.73   
3                96560              95440                 93.79   
4                96560              95450                 96.46   
..                 ...                ...                   ...   
331              96840              95770                 59.76   
332              96860              95780                 57.93   
333              96860              95790                 57.41   
334              96850              95770                 55.16   
335              96870              95790                 56.51   

     surface_precipitation_rate  wind_speed_10m  wind_speed_40m   
0                           0.0            2.94            5.20  \
1                           0.0            3.14            5.34   
2                           0.0            3.21            5.17   
3                           0.0            3.54            5.51   
4                           0.0            3.16            5.49   
..                          ...             ...             ...   
331                         0.0            3.66            7.15   
332                         0.0            3.70            7.21   
333                         0.0            3.54            7.08   
334                         0.0            3.99            7.52   
335                         0.0            3.96            7.47   

     wind_speed_60m  wind_speed_80m  wind_speed_100m  wind_speed_120m   
0              6.00            6.64             7.37             8.11  \
1              6.15            6.81             7.65             8.53   
2              5.98            6.76             7.59             8.40   
3              6.26            6.94             7.53             8.05   
4              6.34            7.02             7.67             8.28   
..              ...             ...              ...              ...   
331            8.63            9.70            10.33            10.61   
332            8.65            9.67            10.36            10.79   
333            8.63            9.64            10.24            10.48   
334            9.02           10.12            10.83            11.23   
335            8.96           10.12            10.92            11.47   

     wind_speed_140m  wind_speed_160m  wind_speed_200m  wind_dir_10m   
0               8.76             9.36            10.32        355.83  \
1               9.31             9.96            10.45        257.65   
2               9.20             9.87            10.49        252.83   
3               8.51             8.90             9.42        353.22   
4               8.65             8.91             8.99        354.50   
..               ...              ...              ...           ...   
331            10.58            10.45            10.14        172.85   
332            10.91            10.92            10.50        172.81   
333            10.41            10.25             9.9

In [11]:
altitudes = [10,40,60,80,100,120,140,160,200]

In [12]:
features = ['air_temp', 'wind_speed', 'wind_dir']
names = ['Temperature','Wind Speed','Wind Direction']
units = ['F','m/s','degrees']

for feat, name, unit in zip(features,names, units):
    feat_df = []
    for season, df in zip(['Summer','Winter'],[summer_data, winter_data]):
        for i, row in df.iterrows():
            for alt in altitudes:
                col_name = f"{feat}_{alt}m"
                val = row[col_name]
                feat_df.append([alt, val, season])
    feat_df = pd.DataFrame(feat_df, columns=['Altitude', name, 'Season'])

    fig = px.box(feat_df, x=name, y='Altitude', color='Season')
    fig.update_traces(orientation='h')
    fig.update_yaxes(
        tickvals=altitudes,
        range=[-10,220],
        title='Altitude (m)'
    )
    fig.update_xaxes(title=f'{name} ({unit})')
    fig.update_layout(title=f'{name} by Altitude')
    fig.show()

In [14]:
fig = go.Figure()

trace1 = go.Scatter(y=summer_data['surface_air_pressure'], x=summer_data['daily_index'], mode='markers', name='000-S')
trace2 = go.Scatter(y=winter_data['surface_air_pressure'], x=winter_data['daily_index'], mode='markers', name='000-W')
trace3 = go.Scatter(y=summer_data['air_pressure_100m'], x=summer_data['daily_index'], mode='markers', name='100-S')
trace4 = go.Scatter(y=winter_data['air_pressure_100m'], x=winter_data['daily_index'], mode='markers', name='100-W')
trace5 = go.Scatter(y=summer_data['air_pressure_200m'], x=summer_data['daily_index'], mode='markers', name='200-S')
trace6 = go.Scatter(y=winter_data['air_pressure_200m'], x=winter_data['daily_index'], mode='markers', name='200-W')

fig.add_trace(trace1)
fig.add_trace(trace2)
fig.add_trace(trace3)
fig.add_trace(trace4)
fig.add_trace(trace5)
fig.add_trace(trace6)

fig.update_xaxes(
    tickvals=[12*i for i in range(5)],
    ticktext=[f'{6*i}:00' for i in range(5)]
)

fig.update_yaxes(title='Pressure')
fig.update_layout(width=1e3, title='Air Pressure over Time')

fig.show()

In [35]:
fig = go.Figure()

summ_press = summer_data.groupby('daily_index').mean()
wint_press = winter_data.groupby('daily_index').mean()

trace1 = go.Scatter(y=summ_press['surface_air_pressure'], x=summ_press.index, mode='markers', name='Surface-Summer')
trace2 = go.Scatter(y=wint_press['surface_air_pressure'], x=wint_press.index, mode='markers', name='Surface-Winter')
trace3 = go.Scatter(y=summ_press['air_pressure_100m'], x=summ_press.index, mode='markers', name='100m-Summer')
trace4 = go.Scatter(y=wint_press['air_pressure_100m'], x=wint_press.index, mode='markers', name='100m-Winter')
trace5 = go.Scatter(y=summ_press['air_pressure_200m'], x=summ_press.index, mode='markers', name='200m-Summer')
trace6 = go.Scatter(y=wint_press['air_pressure_200m'], x=wint_press.index, mode='markers', name='200m-Winter')

fig.add_trace(trace1)
fig.add_trace(trace2)
fig.add_trace(trace3)
fig.add_trace(trace4)
fig.add_trace(trace5)
fig.add_trace(trace6)

fig.update_xaxes(
    tickvals=[12*i for i in range(5)],
    ticktext=[f'{6*i}:00' for i in range(5)]
)

fig.update_yaxes(title='Pressure')
fig.update_layout(width=1e3, title='Air Pressure over Time')

fig.show()

In [61]:
fig = go.Figure()

trace_summer = go.Scatter(x=summer_data['daily_index'], y=summer_data['relative_humidity_2m'], 
                          mode='markers', name="Summer")
trace_winter = go.Scatter(x=winter_data['daily_index'], y=winter_data['relative_humidity_2m'], 
                          mode='markers', name="Winter")

fig.add_trace(trace_summer)
fig.add_trace(trace_winter)


fig.update_xaxes(
    tickvals=[12*i for i in range(5)],
    ticktext=[f'{6*i}:00' for i in range(5)]
)

fig.update_yaxes(title='Relative Humdity at 2m (%)')
fig.update_layout(title='Relative Humidity over Time')

fig.show()

In [62]:
altitudes

[10, 40, 60, 80, 100, 120, 140, 160, 200]

In [9]:
year_data = windtk_api.get_dataframe(t1=(1,1), t2=(12,31))

In [66]:
year_group = year_data.groupby('day_of_year')

In [69]:
peak_data = year_group.max()
trough_data = year_group.min()
avg_data = year_group.mean()

In [114]:
altitudes = [10, 100, 200]

In [123]:
fig = go.Figure()

alt_cnt = len(altitudes)
trues, falses = [True] * alt_cnt, [False] * alt_cnt
peak_visi = trues + falses + falses
trough_visi = falses + trues + falses
avg_visi = falses + falses + trues

peak_button = dict(
    label='Peak',
    method='update',
    args=[{'visible':peak_visi}]
)

trough_button = dict(
    label='Trough',
    method='update',
    args=[{'visible':trough_visi}]
)

avg_button = dict(
    label='Average',
    method='update',
    args=[{'visible':avg_visi}],
)

buttons = [peak_button, trough_button, avg_button]

updatemenus = [dict(
    buttons=buttons,
    showactive=True,
    active=2
)]

for di, df in enumerate([peak_data, trough_data, avg_data]):
    visi = True if di == 2 else False
    for alt in altitudes:
        col = f'wind_speed_{alt}m'
        trace = go.Scatter(x=df.index, y=df[col], name=f'{alt}m', visible=visi)
        fig.add_trace(trace)

        
months = ['Janurary', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 
          'October', 'November', 'December']
month_starts = [1]
for day in range(2,366):
    if year_data.iloc[(day-1)*48].Month != year_data.iloc[(day-2)*48].Month:
        month_starts.append(day)
        
fig.update_xaxes(
    title='Year',
    tickvals=month_starts,
    ticktext=months
)

fig.update_yaxes(
    title='Wind Speed (m/s)'
)
        
fig.update_layout(title='Wind Speeds throughout the year', updatemenus=updatemenus)
        
fig.show()

In [131]:
fig = go.Figure()


for alt in altitudes:
    col = f'wind_dir_{alt}m'
    trace = go.Scatter(x=avg_data.index, y=avg_data[col], name=f'{alt}m')
    fig.add_trace(trace)

        
months = ['Janurary', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 
          'October', 'November', 'December']
month_starts = [1]
for day in range(2,366):
    if year_data.iloc[(day-1)*48].Month != year_data.iloc[(day-2)*48].Month:
        month_starts.append(day)
        
fig.update_xaxes(
    title='Year',
    tickvals=month_starts,
    ticktext=months
)

fig.update_yaxes(title='Wind Direction', 
                 range=[0,360], tickvals=[i*90 for i in range(5)],
                ticktext=['North','East','South','West','North'])
        
fig.update_layout(title='Wind Speeds throughout the year')
        
fig.show()

In [146]:
winter_months = [1,2,12]
spring_months = [3,4,5]
summer_months = [6,7,8]
autumn_months = [9,10,11]

In [147]:
def partition_by_month(months):
    data = []
    for m in months:
        data.append(avg_data.loc[avg_data.Month == m])
    return pd.concat(data)

winter_data = partition_by_month(winter_months)
spring_data = partition_by_month(spring_months)
summer_data = partition_by_month(summer_months)
autumn_data = partition_by_month(autumn_months)

In [173]:
fig = go.Figure()

trace_winter = go.Scatterpolar(theta=winter_data['wind_dir_10m'], r=winter_data['wind_speed_10m'], 
                             mode='markers', name='Winter', showlegend=True)
trace_spring = go.Scatterpolar(theta=spring_data['wind_dir_10m'], r=spring_data['wind_speed_10m'], 
                             mode='markers', name='Spring', showlegend=True)
trace_summer = go.Scatterpolar(theta=summer_data['wind_dir_10m'], r=summer_data['wind_speed_10m'], 
                             mode='markers', name='Summer', showlegend=True)
trace_autumn = go.Scatterpolar(theta=autumn_data['wind_dir_10m'], r=autumn_data['wind_speed_10m'], 
                             mode='markers', name='Autumn', showlegend=True)

fig.add_trace(trace_winter)
fig.add_trace(trace_spring)
fig.add_trace(trace_summer)
fig.add_trace(trace_autumn)

fig.update_layout(
    title='Wind velocities by the Season',
    width=800, height=800,
    polar={
    'angularaxis': {
        'rotation':90,
        'direction':'clockwise',
        'tickvals': [0,   45,  90, 135, 180, 225, 270, 315],
        'ticktext': ['N','NE','E','SE','S','SW','W','NW']
    },
})

fig.show()

In [12]:
windtk_api.calibrate(latitude, longitude, 2013)
windtk_api.download()
windtk_api.tabelize()
year_data_2013 = windtk_api.get_dataframe(t1=(1,1), t2=(12,31))
windtk_api.calibrate(latitude, longitude, 2012)
windtk_api.download()
windtk_api.tabelize()
year_data_2012 = windtk_api.get_dataframe(t1=(1,1), t2=(12,31))

WindTK Data saved as CSV successfully.
WindTK Data saved as CSV successfully.


In [16]:
fig = go.Figure()

trace_2013 = go.Scatter(x=year_data_2013['day_of_year'], y=year_data_2013['wind_speed_200m'])
trace_2012 = go.Scatter(x=year_data_2012['day_of_year'], y=year_data_2012['wind_speed_200m'])

fig.add_trace(trace_2013)
fig.add_trace(trace_2012)

fig.show()